# Chicago TNP Data Exploration

Notes:

- Datasets to updated quarterly
- Starting and ending time rounded to nearest 15 minutes
- Trip fare rounded to nearest $2.50
- Tip rounded to nearest \$1.00

In [60]:
import json
import pandas as pd
import numpy as np
import requests
import geopandas as gpd
import matplotlib as plt
from folium.plugins import HeatMap
from shapely.geometry import shape, Point

In [2]:
d = {'dataset_name': ['Trips', 'Drivers', 'Vehicles'], 'total_obs': [17432011, 4812612, 4812049], 'date_reported_start': ['11/01/2018', '2015-02','2015-02'], 'date_reported_end': ['12/31/2018', '2018-12', '2018-12'], 'num_cols': [21, 7, 9]}
summary_df = pd.DataFrame(d)
summary_df

dataset_name  total_obs date_reported_start date_reported_end  num_cols
0        Trips   17432011          11/01/2018        12/31/2018        21
1      Drivers    4812612             2015-02           2018-12         7
2     Vehicles    4812049             2015-02           2018-12         9

## Trips Dataset

API to get entries from midnight 11/21/2018 to midnight 11/22/2018 & make pandas df

In [27]:
os = 0
params = {'$limit': 1000, '$offset': os}
response = requests.get('https://data.cityofchicago.org/resource/m6dm-c72p.json?$where=trip_start_timestamp%20between%20%272018-11-21T00:00:00.000%27%20and%20%272018-11-22T00:00:00.000%27', params).json()
total_response = response
os = 1000
while len(response) >= 1000:
    params = {'$limit': 1000, '$offset': os}
    response = requests.get('https://data.cityofchicago.org/resource/m6dm-c72p.json?$where=trip_start_timestamp%20between%20%272018-11-21T00:00:00.000%27%20and%20%272018-11-22T00:00:00.000%27', params).json()
    os += 1000
    total_response += response

In [28]:
trips_df = pd.DataFrame.from_dict(total_response, dtype=str)

In [29]:
trips_df.shape

(282375, 21)

Line below is to write out/save json file as to avoid calling requests & waiting for API when reopening notebook:

In [43]:
with open("trips.json", "w") as write_file:
    json.dump(total_response, write_file)

In [18]:
trips_df.columns

Index(['additional_charges', 'dropoff_census_tract',
       'dropoff_centroid_latitude', 'dropoff_centroid_location',
       'dropoff_centroid_longitude', 'dropoff_community_area', 'fare',
       'pickup_census_tract', 'pickup_centroid_latitude',
       'pickup_centroid_location', 'pickup_centroid_longitude',
       'pickup_community_area', 'shared_trip_authorized', 'tip',
       'trip_end_timestamp', 'trip_id', 'trip_miles', 'trip_seconds',
       'trip_start_timestamp', 'trip_total', 'trips_pooled'],
      dtype='object')

In [19]:
trips_df.dtypes

additional_charges            object
dropoff_census_tract          object
dropoff_centroid_latitude     object
dropoff_centroid_location     object
dropoff_centroid_longitude    object
dropoff_community_area        object
fare                          object
pickup_census_tract           object
pickup_centroid_latitude      object
pickup_centroid_location      object
pickup_centroid_longitude     object
pickup_community_area         object
shared_trip_authorized        object
tip                           object
trip_end_timestamp            object
trip_id                       object
trip_miles                    object
trip_seconds                  object
trip_start_timestamp          object
trip_total                    object
trips_pooled                  object
dtype: object

See first five observations in dataset

In [30]:
trips_df.head(n=5)

additional_charges dropoff_census_tract dropoff_centroid_latitude  \
0                2.5                  NaN             41.8390869059   
1               9.33                  NaN                       NaN   
2                2.5                  NaN                       NaN   
3               8.25                  NaN                       NaN   
4                2.5                  NaN                       NaN   

                           dropoff_centroid_location  \
0  {'type': 'Point', 'coordinates': [-87.71400380...   
1                                                NaN   
2                                                NaN   
3                                                NaN   
4                                                NaN   

  dropoff_centroid_longitude dropoff_community_area  fare pickup_census_tract  \
0              -87.714003807                     30   7.5                 NaN   
1                        NaN                    NaN    20                 NaN   
2                        NaN                    NaN    25                 NaN   
3                        NaN                    NaN    20         17031980100   
4                        NaN                    NaN  27.5                 NaN   

  pickup_centroid_latitude                           pickup_centroid_location  \
0                      NaN                                                NaN   
1            41.9802643146  {'type': 'Point', 'coordinates': [-87.91362459...   
2             41.874005383  {'type': 'Point', 'coordinates': [-87.66351754...   
3             41.785998518  {'type': 'Point', 'coordinates': [-87.75093428...   
4            41.8299223039  {'type': 'Point', 'coordinates': [-87.67250264...   

   ... pickup_community_area shared_trip_authorized tip  \
0  ...                   NaN                  False   0   
1  ...                    76                  False   0   
2  ...                    28                  False   5   
3  ...                    56                  False   0   
4  ...                    59                  False   0   

        trip_end_timestamp                                   trip_id  \
0  2018-11-21T00:00:00.000  10e6be997137b6df0d9aa2860de49afa5aa21e65   
1  2018-11-21T00:45:00.000  16e971b8155f0a3f7fab5eddadacdc1d85c6b62b   
2  2018-11-21T00:45:00.000  1815220901f6074659600af59d932be10852f5d5   
3  2018-11-21T00:30:00.000  31f6cad79703c15b04fccfd316447d4f554dd571   
4  2018-11-21T00:30:00.000  77c6f283dd958c8259218d60b986c20343db20a1   

         trip_miles trip_seconds     trip_start_timestamp trip_total  \
0  3.91872777169513          592  2018-11-21T00:00:00.000         10   
1    12.80267943392         2196  2018-11-21T00:00:00.000      29.33   
2    10.36108505008         3022  2018-11-21T00:00:00.000       32.5   
3  13.4386832506784         1396  2018-11-21T00:00:00.000      28.25   
4  23.3605746100459         1714  2018-11-21T00:00:00.000         30   

  trips_pooled  
0            1  
1            1  
2            1  
3            1  
4            1  

[5 rows x 21 columns]

Number of NaN/Null Values by Column

In [31]:
trips_df.isnull().sum(axis=0)

additional_charges                0
dropoff_census_tract          88860
dropoff_centroid_latitude     18310
dropoff_centroid_location     18310
dropoff_centroid_longitude    18310
dropoff_community_area        18491
fare                              0
pickup_census_tract           89732
pickup_centroid_latitude      18828
pickup_centroid_location      18828
pickup_centroid_longitude     18828
pickup_community_area         18935
shared_trip_authorized            0
tip                               0
trip_end_timestamp                0
trip_id                           0
trip_miles                        0
trip_seconds                      0
trip_start_timestamp              0
trip_total                        0
trips_pooled                      0
dtype: int64

For longest value in each column:

In [42]:
longest_val = 0
for column in trips_df.columns:
    for val in trips_df[column].unique():
        if len(str(val)) > longest_val:
            longest_val = len(str(val))
    print(column, longest_val)

additional_charges 5
dropoff_census_tract 11
dropoff_centroid_latitude 13
dropoff_centroid_location 70
dropoff_centroid_longitude 70
dropoff_community_area 70
fare 70
pickup_census_tract 70
pickup_centroid_latitude 70
pickup_centroid_location 70
pickup_centroid_longitude 70
pickup_community_area 70
shared_trip_authorized 70
tip 70
trip_end_timestamp 70
trip_id 70
trip_miles 70
trip_seconds 70
trip_start_timestamp 70
trip_total 70
trips_pooled 70


Converts timestamps from strings to datetime objects

In [32]:
trips_df['trip_start_timestamp'] = pd.to_datetime(trips_df['trip_start_timestamp'])
trips_df['trip_end_timestamp'] = pd.to_datetime(trips_df['trip_end_timestamp'])

Earliest trip start time for obs in df:

In [33]:
trips_df.trip_start_timestamp.min()

Timestamp('2018-11-21 00:00:00')

Latest trip start time for obs in df:

In [34]:
trips_df.trip_start_timestamp.max()

Timestamp('2018-11-22 00:00:00')

Earliest trip end time for obs in df:

In [35]:
trips_df.trip_end_timestamp.min()

Timestamp('2018-11-21 00:00:00')

Latest trip end time for obs in df:

In [36]:
trips_df.trip_end_timestamp.max()

Timestamp('2018-11-22 05:45:00')

Early Morning (00:00:00 to 6:30:00)

In [67]:
early_morning_df = trips_df[trips_df['trip_start_timestamp'] <= '2018-11-21 06:30:00']

Morning Rush (6:30:01 to 10:00:00)

In [73]:
morning_rush_df = trips_df[(trips_df['trip_start_timestamp'] > '2018-11-21 06:30:01') & (trips_df['trip_start_timestamp'] <= '2018-11-21 10:00:00')]

Morning Rush Heatmaps (w/ null locations dropped)

In [69]:
morning_rush_df = morning_rush_df[morning_rush_df['pickup_centroid_latitude'].notnull()]
morning_rush_df = morning_rush_df[morning_rush_df['dropoff_centroid_latitude'].notnull()]

Morning Rush Pickups Heatmap

In [70]:
xy = morning_rush_df[['pickup_centroid_latitude', 'pickup_centroid_longitude']]
hmap = folium.Map(location=[41.87, -87.69], zoom_start=11)
hm_rod = HeatMap(list(zip(xy['pickup_centroid_latitude'].values, xy['pickup_centroid_longitude'].values)), radius=13, blur=20)
hmap.add_child(hm_rod)

Morning Rush Dropoffs Heatmap

In [71]:
xy = morning_rush_df[['dropoff_centroid_latitude', 'dropoff_centroid_longitude']]
hmap = folium.Map(location=[41.87, -87.69], zoom_start=11)
hm_rod = HeatMap(list(zip(xy['dropoff_centroid_latitude'].values, xy['dropoff_centroid_longitude'].values)), radius=12, blur=20)
hmap.add_child(hm_rod)

Midday (10:00:001 to 16:00:00)

In [74]:
midday_df = trips_df[(trips_df['trip_start_timestamp'] > '2018-11-21 10:00:01') & (trips_df['trip_start_timestamp'] <= '2018-11-21 16:00:00')]

Evening Rush (16:00:01 to 19:00:00)

In [76]:
evening_rush_df = trips_df[(trips_df['trip_start_timestamp'] > '2018-11-21 16:00:01') & (trips_df['trip_start_timestamp'] <= '2018-11-21 19:00:00')]

Evening Rush Pickups Heatmap

In [77]:
evening_rush_df = evening_rush_df[evening_rush_df['pickup_centroid_latitude'].notnull()]
evening_rush_df = evening_rush_df[evening_rush_df['dropoff_centroid_latitude'].notnull()]
xy = evening_rush_df[['pickup_centroid_latitude', 'pickup_centroid_longitude']]
hmap = folium.Map(location=[41.87, -87.69], zoom_start=11)
hm_rod = HeatMap(list(zip(xy['pickup_centroid_latitude'].values, xy['pickup_centroid_longitude'].values)), radius=13, blur=20)
hmap.add_child(hm_rod)

Evening Rush Dropoffs Heatmap

In [78]:
xy = evening_rush_df[['dropoff_centroid_latitude', 'dropoff_centroid_longitude']]
hmap = folium.Map(location=[41.87, -87.69], zoom_start=11)
hm_rod = HeatMap(list(zip(xy['dropoff_centroid_latitude'].values, xy['dropoff_centroid_longitude'].values)), radius=13, blur=20)
hmap.add_child(hm_rod)

Late Evening (19:00:01 to 11:59:59)

In [79]:
late_even_df = trips_df[(trips_df['trip_start_timestamp'] > '2018-11-21 19:00:01') & (trips_df['trip_start_timestamp'] <= '2018-11-21 11:59:59')]

## Driver Dataset

API to get first 1,000 (max to download w/o loop) from drivers dataset & make pandas dataframe:

In [71]:
dr_response = requests.get('https://data.cityofchicago.org/resource/j6wf-834c.json').json()
dr_df = pd.DataFrame.from_dict(dr_response)

In [5]:
dr_df.columns

Index(['city', 'driver_start_month', 'month_reported', 'multiple_tnps',
       'number_of_trips', 'state', 'zip'],
      dtype='object')

See first 5 observations in dataset

In [6]:
dr_df.head(n=5)

city driver_start_month month_reported  multiple_tnps number_of_trips  \
0    Aurora            2015-12        2016-08          False             342   
1   Chicago            2017-02        2018-01           True             391   
2    Dolton            2015-03        2018-01           True             371   
3  Eilmette            2017-07        2017-09          False             251   
4   Chicago            2018-02        2018-06          False             332   

  state    zip  
0    IL  60505  
1    IL  60612  
2    IL  60419  
3    IL  60091  
4    IL  60606

Number of NaN/Null Values by Column

In [26]:
dr_df.isnull().sum(axis=0)

city                  40
driver_start_month     0
month_reported         0
multiple_tnps          0
number_of_trips        6
state                  0
zip                   40
dtype: int64

For longest value in each column:

In [27]:
longest_val = 0
for column in dr_df.columns:
    for val in dr_df[column].unique():
        if len(str(val)) > longest_val:
            longest_val = len(str(val))
    print(column, longest_val)

city 20
driver_start_month 20
month_reported 20
multiple_tnps 20
number_of_trips 20
state 20
zip 20


Earliest Driver Start Date in Set Pulled

In [16]:
dr_df.driver_start_month.min()

'2013-08'

Most Recent Driver Start Date in Set Pulled

In [18]:
dr_df.driver_start_month.max()

'2018-06'

Earliest Month Reported in Set Pulled

In [20]:
dr_df.month_reported.min()

'2015-03'

Latest Month Reported in Set Pulled

In [21]:
dr_df.month_reported.max()

'2018-06'

This is interesting that the data is not all most recently reported -- city must have another metric that we cannot see for sorting.

Percentage of Non-Chicago Drivers in Set

In [23]:
nonchi_dr = dr_df[dr_df['city']!= 'Chicago']

In [27]:
(100 * nonchi_dr.shape[0])/dr_df.shape[0]

77.6

Zip Codes of Drivers in Set

In [44]:
dr_df['zip'].unique()

array(['60505', '60612', '60419', '60091', '60606', '60632', '60402',
       '60016', '63020', '98023', '60137', '60409', '60172', '75287',
       '60133', nan, '60707', '60452', '60064', '60415', '60638', '60639',
       '60425', '60456', '60626', '60426', '60112', '60130', '60431',
       '60625', '60458', '60478', '46534', '60517', '60422', '60630',
       '60538', '60077', '60025', '60617', '60653', '60613', '60048',
       '60502', '60071', '60076', '46403', '60136', '60304', '20876',
       '60429', '60139', '60101', '46322', '60804', '60506', '60053',
       '60634', '60603', '60193', '98502', '60628', 'None', '52655',
       '60459', '60467', '60153', '60123', '60637', '60004', '60477',
       '60560', '60622', '60187', '63862', '60090', '60067', '52732',
       '60070', '60110', '60404', '60659', '60085', '60451', '33133',
       '60433', '60174', '60471', '60108', '60188', '60645', '60195',
       '60455', '98118', '60161', '60411', '60171', '60504', '60629',
       '60015', 

Find Invalid Zipcodes

In [66]:
invalid_zips = []
for zip_code in dr_df[dr_df['zip'].notnull()].zip.unique():
    if len(zip_code) < 5:
        invalid_zips.append(zip_code)

In [67]:
invalid_zips

['None', '6515', '6007', '2673']

Find Number of Invalid Zip Codes

In [69]:
num_invalid_zips = 0
for zip_code in invalid_zips:
    num_invalid_zips += dr_df[dr_df['zip'] == zip_code].shape[0]

In [70]:
num_invalid_zips

4

(double check)

In [60]:
dr_df['zip'].where(dr_df['zip'].str.len() < 5).count()

4

Drop Invalid & Null Zip Codes

In [77]:
cleaned_dr_df = dr_df[~dr_df['zip'].isin(invalid_zips)]
cleaned_dr_df = cleaned_dr_df[cleaned_dr_df['zip'].notnull()]

# Vehicle Dataset

API to get first 1,000 (max to download w/o loop) from vehicles dataset & make pandas dataframe:

In [7]:
vehicle_response = requests.get('https://data.cityofchicago.org/resource/bc6b-sq4u.json').json()
vehicle_df = pd.DataFrame.from_dict(dr_response)

In [8]:
vehicle_df.columns

Index(['city', 'driver_start_month', 'month_reported', 'multiple_tnps',
       'number_of_trips', 'state', 'zip'],
      dtype='object')

See first 5 observations in dataset

In [9]:
vehicle_df.head(n=5)

city driver_start_month month_reported  multiple_tnps number_of_trips  \
0    Aurora            2015-12        2016-08          False             342   
1   Chicago            2017-02        2018-01           True             391   
2    Dolton            2015-03        2018-01           True             371   
3  Eilmette            2017-07        2017-09          False             251   
4   Chicago            2018-02        2018-06          False             332   

  state    zip  
0    IL  60505  
1    IL  60612  
2    IL  60419  
3    IL  60091  
4    IL  60606

Number of NaN/Null Values by Column

In [31]:
vehicle_df.isnull().sum(axis=0)

city                  40
driver_start_month     0
month_reported         0
multiple_tnps          0
number_of_trips        6
state                  0
zip                   40
dtype: int64

For longest value in each column:

In [32]:
longest_val = 0
for column in vehicle_df.columns:
    for val in vehicle_df[column].unique():
        if len(str(val)) > longest_val:
            longest_val = len(str(val))
    print(column, longest_val)

city 20
driver_start_month 20
month_reported 20
multiple_tnps 20
number_of_trips 20
state 20
zip 20
